## Introduction to Machine Learning  

## Assignment 5: Preprocessing Numerical Features, Pipelines and Hyperparameter Optimization

You can't learn technical subjects without hands-on practice. The assignments are an important part of the course. To submit this assignment you will need to make sure that you save your Jupyter notebook. 

Below are the links of 2 videos that explain:

1. [How to save your Jupyter notebook](https://youtu.be/0aoLgBoAUSA) and,       
2. [How to answer a question in a Jupyter notebook assignment](https://youtu.be/7j0WKhI3W4s).

### Assignment Learning Goals:

By the end of the module, students are expected to:

- Identify when to implement feature transformations such as imputation and scaling.
- Apply `sklearn.pipeline.Pipeline` to build a machine learning pipeline.
- Use `sklearn` for applying numerical feature transformations on the data.
- Discuss the golden rule in the context of feature transformations.
- Carry out hyperparameter optimization using `sklearn`'s `GridSearchCV` and `RandomizedSearchCV`.
- Explain overfitting on the validation set.


This assignment covers [Module 5](https://ml-learn.mds.ubc.ca/en/module5) of the online course. You should complete this module before attempting this assignment.

Any place you see `...`, you must fill in the function, variable, or data to complete the code. Substitute the `None` with your completed code and answers then proceed to run the cell!

Note that some of the questions in this assignment will have hidden tests. This means that no feedback will be given as to the correctness of your solution. It will be left up to you to decide if your answer is sufficiently correct. These questions are worth 2 points.

In [1]:
# Import libraries needed for this lab
from hashlib import sha1

import altair as alt
import graphviz
import numpy as np
import pandas as pd

from sklearn import tree
from sklearn.dummy import DummyClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split, cross_validate
from sklearn.neighbors import KNeighborsClassifier
from sklearn.impute import SimpleImputer
from sklearn.pipeline import Pipeline, make_pipeline
from sklearn.preprocessing import (
    FunctionTransformer,
    Normalizer,
    OneHotEncoder,
    StandardScaler,
    normalize,
    scale)
from sklearn.svm import SVC

import test_assignment5 as t
#alt.renderers.enable('mimetype')
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

## 1. Introducing and Exploring the dataset <a name="1"></a>
<hr>


In this lab you will be working on a sample of [the adult census dataset](https://www.kaggle.com/uciml/adult-census-income#). We have made some modification to this data so that it's easier to work with. 

This is a classification dataset and the classification task is to predict whether income exceeds 50K per year or not based on the census data. You can find more information on the dataset and features [here](http://archive.ics.uci.edu/ml/datasets/Adult).


*Note that many popular datasets have sex as a feature where the possible values are male and female. This representation reflects how the data were collected and is not meant to imply that, for example, gender is binary.*

In [2]:
census_df = pd.read_csv("data/income.csv")
display(census_df.head())

age workclass  fnlwgt     education  education_num  marital_status  \
0   74         0   88638     Doctorate             16               0   
1   41         1   70037  Some-college             10               0   
2   45         1  172274     Doctorate             16               5   
3   38         2  164526   Prof-school             15               0   
4   52         1  129177     Bachelors             13               6   

       occupation    relationship   race  sex  capital_gain  capital_loss  \
0  Prof-specialty  Other-relative  White    0             0          3683   
1    Craft-repair       Unmarried  White    1             0          3004   
2  Prof-specialty       Unmarried  Black    0             0          3004   
3  Prof-specialty   Not-in-family  White    1             0          2824   
4   Other-service   Not-in-family  White    0             0          2824   

   hrs_per_week native.country income  
0            20  United-States   >50K  
1            60              ?   >50K  
2            35  United-States   >50K  
3            45  United-States   >50K  
4            20  United-States   >50K

For this assignment, we will be looking at the numeric columns only and then we will look into the both the categorical and numeric columns in the following assignment after we've learned how to preprocess them in module 6. 

In [3]:
census_df = census_df.drop(columns = ['education', 'occupation', 'relationship', 'race', 'native.country'])
display(census_df.head())

age workclass  fnlwgt  education_num  marital_status  sex  capital_gain  \
0   74         0   88638             16               0    0             0   
1   41         1   70037             10               0    1             0   
2   45         1  172274             16               5    0             0   
3   38         2  164526             15               0    1             0   
4   52         1  129177             13               6    0             0   

   capital_loss  hrs_per_week income  
0          3683            20   >50K  
1          3004            60   >50K  
2          3004            35   >50K  
3          2824            45   >50K  
4          2824            20   >50K

**Question 1.1** <br> {points: 1}  

In order to avoid violation of the golden rule, the first step before we do anything is splitting the data. 

Split the data into `train_df` (80%) and `test_df` (20%). Keep the target column (`income`) in the splits so that we can use it in EDA. Make sure to set `random_state=123` for grading purposes. 


In [4]:
train_df, test_df = train_test_split(census_df, test_size = 0.2, random_state = 123)

In [5]:
t.test_1_1(train_df,test_df)

'Success'

**Question 1.2** <br> {points: 1}  

Let's examine our train_df column dtypes. 

Do you notice anything odd? Which column needs further investigation? 

*Answer in the cell below by place the column label in `""` and assign it to an object called `answer1_2`.*


In [6]:
train_df.dtypes

age                int64
workclass         object
fnlwgt             int64
education_num      int64
marital_status     int64
sex                int64
capital_gain       int64
capital_loss       int64
hrs_per_week       int64
income            object
dtype: object

In [7]:
answer1_2 = 'workclass'

In [8]:
t.test_1_2(answer1_2)

'Success'

**Question 1.3** <br> {points: 1}  

Take a look at the unique possible values in this column using [`.unique()`](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.unique.html) or `.value_counts()`. 

Which value is not numerical? Save this value as a string by placing it between `""` and assigning it to an object called `answer1_3`.

In [9]:
def return_unconverted(val) :
    try : 
        converted = int(val)
    except ValueError:
        return val

In [10]:
answer1_3 = [return_unconverted(val) for val in train_df['workclass'].unique() if return_unconverted(val) is not None][0]
print(answer1_3)

?


In [11]:
t.test_1_3(answer1_3)

'Success'

**Question 1.4** <br> {points: 1}  

Looking at the previous question, these values were likely questions not answered by some people during the census.

Usually `.describe()` or `.info()` methods would give you information on missing values. But here, they won't pick up this value as missing values as they are encoded as strings instead of an actual NaN in Python.

Let's replace them with `np.NaN` before we carry out EDA. Name your new `train_df` `test_df` dataframes with the replaced values `train_df_nan` and `test_df_nan` respectively. If you do not do it, you'll encounter an error later on when you try to pass this data to a classifier. 


In [12]:
train_df.describe()

age        fnlwgt  education_num  marital_status  \
count  12545.000000  1.254500e+04   12545.000000    12545.000000   
mean      40.520367  1.884797e+05      10.612515        1.423994   
std       12.857134  1.046215e+05       2.607012        1.637603   
min       17.000000  1.487800e+04       1.000000        0.000000   
25%       31.000000  1.180580e+05       9.000000        1.000000   
50%       40.000000  1.769690e+05      10.000000        1.000000   
75%       49.000000  2.339330e+05      13.000000        1.000000   
max       90.000000  1.484705e+06      16.000000        6.000000   

                sex  capital_gain  capital_loss  hrs_per_week  
count  12545.000000  12545.000000  12545.000000  12545.000000  
mean       0.729853   2080.349223    125.559665     42.130490  
std        0.444054  10498.881446    483.414425     12.074596  
min        0.000000      0.000000      0.000000      1.000000  
25%        0.000000      0.000000      0.000000     40.000000  
50%        1.000000      0.000000      0.000000     40.000000  
75%        1.000000      0.000000      0.000000     50.000000  
max        1.000000  99999.000000   4356.000000     99.000000

In [13]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 12545 entries, 11981 to 3582
Data columns (total 10 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   age             12545 non-null  int64 
 1   workclass       12545 non-null  object
 2   fnlwgt          12545 non-null  int64 
 3   education_num   12545 non-null  int64 
 4   marital_status  12545 non-null  int64 
 5   sex             12545 non-null  int64 
 6   capital_gain    12545 non-null  int64 
 7   capital_loss    12545 non-null  int64 
 8   hrs_per_week    12545 non-null  int64 
 9   income          12545 non-null  object
dtypes: int64(8), object(2)
memory usage: 1.3+ MB


In [14]:
train_df_nan = train_df.assign(workclass = train_df['workclass'].replace('?', np.nan))
test_df_nan = test_df.assign(workclass = test_df['workclass'].replace('?', np.nan))

In [15]:
t.test_1_4(train_df_nan, test_df_nan)

'Success'

**Question 1.5** <br> {points: 1}  

Now, that we've replaced the string values with a numerical value (`NaN` is a float), transform this column to dtype `float64`. Save it as the same column name in the original `train_df_nan` and `test_df_nan` dataframes.

In [16]:
train_df_nan = train_df_nan.assign(workclass = train_df_nan['workclass'].astype('float64'))
test_df_nan = test_df_nan.assign(workclass = test_df_nan['workclass'].astype('float64'))

In [17]:
t.test_1_5(train_df_nan, test_df_nan)

'Success'

**Question 1.6** <br> {points: 1}  

Use `.describe()` to show summary statistics of each feature in the `train_df_nan` dataframe. Save this in an object named `train_stats`. 

In [18]:
train_stats = train_df_nan.describe()
display(train_stats)

age     workclass        fnlwgt  education_num  \
count  12545.000000  11991.000000  1.254500e+04   12545.000000   
mean      40.520367      1.562922  1.884797e+05      10.612515   
std       12.857134      1.249396  1.046215e+05       2.607012   
min       17.000000      0.000000  1.487800e+04       1.000000   
25%       31.000000      1.000000  1.180580e+05       9.000000   
50%       40.000000      1.000000  1.769690e+05      10.000000   
75%       49.000000      2.000000  2.339330e+05      13.000000   
max       90.000000      6.000000  1.484705e+06      16.000000   

       marital_status           sex  capital_gain  capital_loss  hrs_per_week  
count    12545.000000  12545.000000  12545.000000  12545.000000  12545.000000  
mean         1.423994      0.729853   2080.349223    125.559665     42.130490  
std          1.637603      0.444054  10498.881446    483.414425     12.074596  
min          0.000000      0.000000      0.000000      0.000000      1.000000  
25%          1.000000      0.000000      0.000000      0.000000     40.000000  
50%          1.000000      1.000000      0.000000      0.000000     40.000000  
75%          1.000000      1.000000      0.000000      0.000000     50.000000  
max          6.000000      1.000000  99999.000000   4356.000000     99.000000

In [19]:
t.test_1_6(train_stats)

'Success'

**Question 1.7** <br> {points: 2}  

What was highest capital loss someone reported? Save this in an object named `cap_loss_high`. 

What is the average number of years people reported of spending time on their education? Save this in an object named `edu_avg_yrs`. 

In [20]:
cap_loss_high = train_stats.loc['max', 'capital_loss']
edu_avg_yrs = train_stats.loc['mean', 'education_num']

display(f'Capital Loss High : {cap_loss_high}')
display(f'Education Average Years : {edu_avg_yrs}')

'Capital Loss High : 4356.0'

'Education Average Years : 10.612514946193702'

In [21]:
# check that the variable exists
assert 'cap_loss_high' in globals(
), "Please make sure that your solution is named 'cap_loss_high'"

# This test has been intentionally hidden. It will be up to you to decide if your solution
# is sufficiently good.

In [22]:
t.test_1_7_2(edu_avg_yrs)

'Success'

**Question 1.8** <br> {points: 1} 

We have provided you with some visualization of the features values plotted as histograms. 

In [23]:
def plot_histogram(df,feature):
    """
    Plots a Histogram of a Decision Trees Feature

    Parameters
    ----------
    feature: str
        the feature name
    Returns
    -------
    altair.vegalite.v3.api.Chart
        an Altair histogram 
    """

    histogram = alt.Chart(df).mark_bar(
        opacity = 0.7).encode(
        alt.X(str(feature) + str(':O'), bin = alt.Bin(maxbins = 50)),
        alt.Y('count()', stack = None),
        alt.Color('income:N')).properties(
        title = str.title(feature))
    return histogram

feature_list = train_stats.columns[:3]
figure_dict = dict()

for feature in feature_list:
    train_df_nan = train_df_nan.sort_values('income')
    figure_dict.update({feature:plot_histogram(train_df_nan, feature)})
figure_panel = alt.vconcat(*figure_dict.values())

display(figure_panel)

c:\Users\Muntakim\AppData\Local\Programs\Python\Python310\lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.VConcatChart(...)

Given these features, which seems the most relevant for the given prediction task? 

*Assign `answer1_8` the the column label name as an string. in a list and save it as an object named `answer1_8`*.
*For example if you believe the answer is `age`, your answer would like this:*  

`answer1_8 = 'age'`

In [24]:
answer1_8 = 'age'

In [25]:
t.test_1_8(answer1_8)

'Success'

**Question 1.9** <br> {points: 1} 

Let's now separate feature vectors from the targets.  Create `X_train`, `y_train`, `X_test`, `y_test` from `train_df_nan` and `test_df_nan`.


In [26]:
X_train = train_df_nan.drop(columns = ['income'])
y_train = train_df_nan['income']

X_test = test_df_nan.drop(columns = ['income'])
y_test = test_df_nan['income']

In [27]:
t.test_1_9(X_train, X_test, y_train, y_test)

'Success'

**Question 1.10** <br> {points: 1} 

At this point, if you train [`sklearn`'s `SVC`](https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html) model on `X_train` and `y_train` would it work? 

A) Yes, it would train but we make not get meaningful results without scaling. 

B) Yes, it would train and it may give results that are descent enough. 

C) No, it can't train since we have not scaled yet. 

D) No, it can't train since we have not imputed yet.

*Answer in the cell below using the uppercase letter associated with your answer. Place your answer between `""`, assign the correct answer to an object called `answer1_10`.*

In [28]:
answer1_10 = 'D'

In [29]:
t.test_1_10(answer1_10)

'Success'

## 2. Preprocessing - Imputation and Scaling without Pipelines


**Question 2.1** <br> {points: 1}  

Before preprocessing our data, build a dummy classifier using `strategy="prior"`. Carry out 5-fold cross validation on `X_train` and `y_train` using ` cross_validate()`. Don't forget to include the training_score. 

Save the results in a dataframe named `dummy_scores`. 

In [30]:
dummy_scores = pd.DataFrame(
    cross_validate(
        estimator = DummyClassifier(strategy = 'prior'), 
        X = X_train, y = y_train, 
        cv = 5, 
        return_train_score = True
    )
)

display(dummy_scores)

fit_time  score_time  test_score  train_score
0  0.031002    0.025993    0.500598     0.500697
1  0.021997    0.015002    0.500598     0.500697
2  0.022986    0.016007    0.500598     0.500697
3  0.020015    0.014989    0.500598     0.500697
4  0.020989    0.014994    0.500996     0.500598

In [31]:
t.test_2_1(dummy_scores)

'Success'

**Question 2.2** <br> {points: 1}  

Now impute missing values **without** using `sklearn.pipeline.Pipeline`.

In this exercise you'll be imputing missing values **without using `scikit-learn` pipelines**. 

The goal here is two-fold. First, to understand what happens under the hood when you use `scikit-learn` `Pipelines`, and second, to convince yourself why it's a good idea to use pipelines.  

For numeric features, use [`scikit-learn`'s `SimpleImputer`](https://scikit-learn.org/stable/modules/generated/sklearn.impute.SimpleImputer.html) to impute `NaN` values with `strategy="median"`. Remember to apply the transformations on both the train and test splits.  

Save your `SimpleImputer()` in an object named `imp`. Next transform `X_train` and `X_test` using `imp` and save the results in objects named `X_imp_train` and `X_imp_test` respectively.


In [32]:
imp = SimpleImputer(strategy = 'median')

X_imp_train = imp.fit_transform(X_train)
X_imp_test = imp.transform(X_test)

In [33]:
t.test_2_2(imp, X_imp_train, X_imp_test)

'Success'

**Question 2.3** <br> {points: 2}  

When using the `SimpleImputer` transformer on the numeric columns, is there any problem with calling `fit_transform` on the test split? Why or why not? 

A) It is not problematic. 

B) It is problematic because it will imputing missing values with wrong values.

C) It is problematic because we should never call fit on test data.

D) It is problematic because it will throw an error in the code.

*Answer in the cell below using the uppercase letter associated with your answer. Place your answer between `""`, assign the correct answer to an object called `answer2_3`.*


In [34]:
answer2_3 = 'C'

In [35]:
# check that the variable exists
assert 'answer2_3' in globals(
), "Please make sure that your solution is named 'answer2_3'"

# This test has been intentionally hidden. It will be up to you to decide if your solution
# is sufficiently good.

**Question 2.4** <br> {points: 1}  

Carry out cross validation using `cross_validate` on the preprocessed `X_imp_train` and `y_train` using the [KNeighborsClassifier](https://scikit-learn.org/stable/modules/generated/sklearn.neighbors.KNeighborsClassifier.html?highlight=kneighborsclassifier#sklearn.neighbors.KNeighborsClassifier) with default hyperparameters.
Save your results in a dataframe named `scores`. 

In [36]:
scores = pd.DataFrame(
    cross_validate(
        estimator = KNeighborsClassifier(),
        X = X_imp_train, y = y_train,
        cv = 5,
        return_train_score = True
    )
)

display(scores)

fit_time  score_time  test_score  train_score
0  0.112000    0.396997    0.593862     0.736748
1  0.088991    0.358008    0.583898     0.743224
2  0.109003    0.354015    0.597051     0.737744
3  0.101562    0.391006    0.583499     0.743922
4  0.088003    0.347984    0.594261     0.740036

In [37]:
t.test_2_4(scores)

'Success'

**Question 2.5** <br> {points: 1}  

Are we violating the golden rule when we call `cross_validate` in 2.2? Why or why not? 

A) Yes, we are violating the golden rule since our test data is influencing our validation data. 

B) Yes, we are violating the Golden Rule because `cross_validate` is splitting the data after we already transformed it.

C) No we are not violating the golden rule since our test data and training data are not influencing one another. 

D) No we are not violating the golden rule since our validation data is not being influenced by the training phase.

*Answer in the cell below using the uppercase letter associated with your answer. Place your answer between `""`, assign the correct answer to an object called `answer2_5`.*


In [38]:
answer2_5 = 'B'

In [39]:
t.test_2_5(answer2_5)

'Success'

# 3. Preprocessing - Imputation and Scaling with Pipelines

**Question 3.1** <br> {points: 1}  

In this question we are going to build a pipeline for multiple classifiers and append the results to a dictionary named `results_dict`.

In this question we've written the most of the code for you. You will need to fill in the blank so that the code executes and produces a dataframe containing the statistics for each model. 

Make sure that the pipeline includes the transformers `SimpleImputer()` and `StandardScaler()`. 


In [40]:
results_dict = {
    'Dummy': {
        'mean_train_accuracy' : round(dummy_scores["train_score"].mean(),4),
        'mean_validation_accuracy': round(dummy_scores["test_score"].mean(),4),
        'mean_fit_time (s)': round(dummy_scores["fit_time"].mean(),4),
        'mean_score_time (s)': round(dummy_scores["score_time"].mean(),4)
    }
}

models = {
    "Decision tree": DecisionTreeClassifier(),
    "kNN": KNeighborsClassifier(),
    "RBF SVM": SVC(),
}

for model_name, model in models.items():
    print(model_name, ":")
    
    pipe = Pipeline(steps = 
        [
            # Transformers
            ("imputer", SimpleImputer(strategy = 'median')),
            ("scaler", StandardScaler()), 
            # Classifier
            ("classifier", model)
        ]
    )
    
    scores = pd.DataFrame(
        cross_validate(
            estimator = pipe, 
            X = X_train, y = y_train,
            cv = 5, 
            return_train_score = True
        )
    )
    
    results_dict[model_name] ={
        'mean_train_accuracy' : scores["train_score"].mean().round(4),
        'mean_validation_accuracy': scores["test_score"].mean().round(4),
        'mean_fit_time (s)': scores["fit_time"].mean().round(4),
        'mean_score_time (s)': scores["score_time"].mean().round(4)
    }

results_df = pd.DataFrame(results_dict).T
display(results_df)

Decision tree :
kNN :
RBF SVM :


mean_train_accuracy  mean_validation_accuracy  \
Dummy                       0.5007                    0.5007   
Decision tree               0.9999                    0.7655   
kNN                         0.8493                    0.7884   
RBF SVM                     0.8239                    0.8132   

               mean_fit_time (s)  mean_score_time (s)  
Dummy                     0.0234               0.0174  
Decision tree             0.1262               0.0142  
kNN                       0.0884               0.6284  
RBF SVM                   8.3821               4.5137

In [41]:
t.test_3_1(results_df)

'Success'

**Question 3.2** <br> {points: 1}  

Which model produced the best score without hyperparameter tuning? 
Save you answer in an object named `highest_score`. 


In [42]:
highest_score = results_df[results_df['mean_validation_accuracy'] == results_df['mean_validation_accuracy'].max()].index[0]
display(f'The model with the highest validation accuracy is {highest_score}.')

'The model with the highest validation accuracy is RBF SVM.'

In [43]:
t.test_3_2(highest_score)

'Success'

**Question 3.3** <br> {points: 1}  

Which model appears to overfit the most? 
Save you answer in an object named `most_overfit`. 


In [44]:
most_overfit = results_df[results_df['mean_train_accuracy'] - results_df['mean_validation_accuracy'] == (results_df['mean_train_accuracy'] - results_df['mean_validation_accuracy']).max()].index[0]
display(f'The model with the highest difference between training and validation accuracy is {most_overfit}.')  

'The model with the highest difference between training and validation accuracy is Decision tree.'

In [45]:
t.test_3_3(most_overfit)

'Success'

**Question 3.4** <br> {points: 2}  

Which model takes the most time to fit? 
Save you answer in an object named `longest_fit`. 


In [46]:
longest_fit = results_df[results_df['mean_fit_time (s)'] == results_df['mean_fit_time (s)'].max()].index[0]
display(f'The model with the longest fit time is {longest_fit}.')

'The model with the longest fit time is RBF SVM.'

In [47]:
# check that the variable exists
assert 'longest_fit' in globals(
), "Please make sure that your solution is named 'longest_fit'"

# This test has been intentionally hidden. It will be up to you to decide if your solution
# is sufficiently good.

# 4. Hyperparameter Optimization

Now that we have preprocessed features, and explored different models we are ready find optimal hyperparameters. 

**Question 4.1** <br> {points: 0}  
Import `GridSearchCV` and `RandomizedSearchCV` from the appropriate library. 

In [48]:
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

In [49]:
t.test_4_1()

'Success'

**Question 4.2** <br> {points: 1}  

In this question you will tune the `n_neighbors` hyperparameter from the K-NN model. 

1. Create a pipeline with the steps `SimpleImputer(strategy="median")`, `StandardScaler()` and  `KNeighborsClassifier()`in an object named `knn_pipe`.
1. Sweep over the hyperparameters in `param_grid` in [`GridSearchCV`](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.GridSearchCV.html)(`param_grid` is given in the code below) and use 5-fold cross-validation. Similar to `cross_validate` you can pass `return_train_score=True` to your `GridSearchCV` object. Save this in an object named `k_search`. 
1. Fit `k_search` on `X_train` and `y_train`.

*Hint: Setting `n_jobs=-1` should speed it up. This will take about 2 minutes to run.*


In [50]:
param_grid = {
    "knn__n_neighbors": np.arange(1, 50, 10)
}

knn_pipe = Pipeline(steps =
    [
        # Transformers
        ("imputer", SimpleImputer(strategy = "median")),
        ("scaler", StandardScaler()),
        # Model
        ("knn", KNeighborsClassifier())
    ]
)

k_search = GridSearchCV(
    estimator = knn_pipe,
    param_grid = param_grid,
    cv = 5,
    return_train_score = True,
    n_jobs = -1
)

k_search.fit(X_train, y_train)

display(k_search)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('imputer',
                                        SimpleImputer(strategy='median')),
                                       ('scaler', StandardScaler()),
                                       ('knn', KNeighborsClassifier())]),
             n_jobs=-1,
             param_grid={'knn__n_neighbors': array([ 1, 11, 21, 31, 41])},
             return_train_score=True)

In [51]:
t.test_4_2(k_search)

'Success'

**Question 4.3** <br> {points: 4}  

What is the best hyperparameter value for knn? Save it in an object named `best_k`. 

What was the corresponding validation score for it? Save this in an object named `best_k_score`. 

Does this model do better than without hyperparameter tuning `n_neighbors`?   <br> 
Answer as `True` or `False` in an object named `better_model`.


<br> 

*Hint: `.best_params_`  and `.best_score_` are helpful here.* 

In [52]:
best_k = k_search.best_params_['knn__n_neighbors']
print(f'The best value of k is {best_k}.')

best_k_score = k_search.best_score_
print(f'The best validation accuracy is {best_k_score}.')

display(k_search.best_estimator_)

The best value of k is 21.
The best validation accuracy is 0.7976883220406537.


Pipeline(steps=[('imputer', SimpleImputer(strategy='median')),
                ('scaler', StandardScaler()),
                ('knn', KNeighborsClassifier(n_neighbors=21))])

In [53]:
untuned_score = results_df.loc['kNN', 'mean_validation_accuracy'] 
print(f'The untuned kNN validation accuracy is {untuned_score}.')

The untuned kNN validation accuracy is 0.7884.


In [54]:
better_model = best_k_score > untuned_score
print(f'The answer is {better_model}.')

The answer is True.


In [55]:
t.test_4_3_1(best_k)

'Success'

In [56]:
t.test_4_3_2(best_k_score)

'Success'

In [57]:
# check that the variable exists
assert 'better_model' in globals(
), "Please make sure that your solution is named 'better_model'"

# This test has been intentionally hidden. It will be up to you to decide if your solution
# is sufficiently good.

**Question 4.4** <br> {points: 1} 

Ok, let's step it up a notch and tune 2 hyperparameters at once and this time using [`RandomizedSearchCV`](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html?highlight=randomizedsearchcv). 

This time let's find the optimal `gamma` and `C` values for a SVC model. 

1. Create a pipeline saving with the steps `SimpleImputer(strategy="median")`, `StandardScaler()` and  `SVC()`in an object named `svc_pipe`.
1. Sweep over the hyperparameters in `param_grid` in [`RandomizedSearchCV`](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html?highlight=randomizedsearchcv) (again, `param_grid` is given in the code below) and use 5-fold cross-validation and specify `n_iter` to 5. Similar to `cross_validate` you can pass `return_train_score=True`  in `RandomizedSearchCV()`. Make sure to set `random_state=77` in `RandomizedSearchCV` or you will not pass the autograder. Save this in an object named `svc_search`. 
1. Fit `svc_search` on `X_train` and `y_train`.

*Hint: Setting `n_jobs=-1` should speed it up but it may still take around 5 minutes to run. You may want to set `verbose=2` here.*

In [58]:
param_grid = {
    "svc__C" : [0.01, 0.1, 1, 10, 100],
    "svc__gamma" : [0.01, 0.1, 1, 10, 100]
}

svc_pipe = Pipeline(steps =
    [
        # Transformers
        ("imputer", SimpleImputer(strategy = "median")),
        ("scaler", StandardScaler()),
        # Model
        ("svc", SVC())
    ]
)

svc_search = RandomizedSearchCV(
    estimator = svc_pipe,
    param_distributions = param_grid,
    cv = 5, n_iter = 5,
    random_state = 77,
    return_train_score = True,
    n_jobs = -1, verbose = 2
)

svc_search.fit(X_train, y_train)
display(svc_search)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('imputer',
                                              SimpleImputer(strategy='median')),
                                             ('scaler', StandardScaler()),
                                             ('svc', SVC())]),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'svc__C': [0.01, 0.1, 1, 10, 100],
                                        'svc__gamma': [0.01, 0.1, 1, 10, 100]},
                   random_state=77, return_train_score=True, verbose=2)

In [59]:
t.test_4_4(svc_search)

'Success'

**Question 4.5** <br> {points: 2}  

What is the best hyperparameter value for the svc model? Save it in an object named `best_svc`. 

What was the corresponding validation score for it? Save this in an object named `best_svc_score`. 

*Hint: `.best_params_`  and `.best_score_` are helpful here.* 

In [60]:
best_svc = svc_search.best_params_
print(f'The best value of C is {best_svc["svc__C"]} and the best value of gamma is {best_svc["svc__gamma"]}.')

best_svc_score = svc_search.best_score_
print(f'The best validation accuracy is {best_svc_score}.') 

The best value of C is 10 and the best value of gamma is 0.1.
The best validation accuracy is 0.8151454762853728.


In [61]:
t.test_4_5_1(best_svc)

'Success'

In [62]:
t.test_4_5_2(svc_search, best_svc_score)

'Success'

**Question 4.6** <br> {points: 1}  

***True or False***


The `SVC` model without default hyperparameters scores higher.


*Answer in the cell below by assigning `True` or `False` to an object called `answer4_6`.*


In [63]:
answer4_6 = best_svc_score > untuned_score
print(f'The answer is {answer4_6}.')

The answer is True.


In [64]:
t.test_4_6(answer4_6)

'Success'

# 5. Evaluating on the test set <a name="5"></a>
<hr>

Now that we have a best performing model, it's time to assess our model on the set aside test set. In this exercise you'll examine whether the results you obtained using cross-validation on the train set are consistent with the results on the test set. 


**Question 5.1** <br> {points: 1} 

What is the training score of the best scoring model? Save the result in an object named `train_score`. 

In [65]:
best_pipeline = svc_search.best_estimator_

In [66]:
train_score = best_pipeline.fit(X_train, y_train).score(X_train, y_train)
print(f'The mean training accuracy is {train_score}.')

The mean training accuracy is 0.8343563172578716.


In [67]:
t.test_5_1(train_score)

'Success'

**Question 5.2** <br> {points: 1} 


What is the test score of the best model? 

Score best model on `X_test` and `y_test`. 

Save the result in an object named `test_score`. 


In [68]:
test_score = best_pipeline.score(X_test, y_test)
print(f'The mean test accuracy is {test_score}.')

The mean test accuracy is 0.8157475294867708.


In [69]:
t.test_5_2(test_score)

'Success'

## Before Submitting 

Before submitting your assignment please do the following:

- Read through your solutions
- **Restart your kernel and clear output and rerun your cells from top to bottom** 
- Makes sure that none of your code is broken 
- Verify that the tests from the questions you answered have obtained the output "Success"

This is a simple way to make sure that you are submitting all the variables needed to mark the assignment. This method should help avoid losing marks due to changes in your environment.  

## Attributions
- The adult census dataset - [Kaggle](https://www.kaggle.com/uciml/adult-census-income#)


- MDS DSCI 571 - Supervised Learning I - [MDS's GitHub website](https://github.com/UBC-MDS/DSCI_571_sup-learn-1) 
